<a href="https://colab.research.google.com/github/spqr-86/notebooks/blob/main/Movie_Recommender.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<h1>Movie recommendation system</h1>

<h2>I. Introduction</h2>
<p>The goal of this data science project is to create a movie recommendation system based on the MovieLens dataset. This dataset contains 20000263 ratings and 465564 tag applications across 27278 movies, collected from 138493 users between January 09, 1995, and March 31, 2015. The data was generated on October 17, 2016.</p>

<p>MovieLens is a popular movie recommendation service that provides users with personalized movie recommendations based on their preferences. This dataset includes user ratings and free-text tagging activities, which can be used to train a recommendation system that can predict which movies a user is likely to enjoy.</b>

<b>Data Description:</b>

<p>The MovieLens dataset contains a total of 20000263 ratings and 465564 tag applications across 27278 movies. The ratings range from 0.5 to 5, and users were selected at random for inclusion. All selected users had rated at least 20 movies. The dataset also includes information on the movies, such as their titles, genres, and release years.</p>

<b>Objective:</b>

<p>The objective of this project is to build a movie recommendation system that can provide personalized movie recommendations to users based on their preferences. To achieve this, we will first explore and preprocess the data to ensure that it is clean and ready for analysis. We will then use various machine learning techniques, such as collaborative filtering and content-based filtering, to train and evaluate the recommendation system.</p>

<b>Conclusion:</b>

<p>In summary, this data science project aims to build a movie recommendation system based on the MovieLens dataset. By analyzing user ratings and free-text tagging activities, we can develop a system that can predict which movies a user is likely to enjoy. This project has the potential to provide valuable insights into the field of recommendation systems and can be extended to other domains such as music, books, and more.</p>

<h2>Table of Contents</h2>
<div class="alert alert-block alert-info" style="margin-top: 20px">
	<ol type="I">
		<li><a href="#introduction">Introduction</a></li>
		<li><a href="#data-preprocessing">Data Preprocessing</a></li>
		<li><a href="#collaborative-filtering">Collaborative Filtering</a></li>
		<li><a href="#content-based-filtering">Content-Based Filtering</a></li>
		<li><a href="#hybrid-recommender-systems">Hybrid Recommender Systems</a></li>
		<li><a href="#conclusion">Conclusion</a></li>
		<li><a href="#references">References</a></li>
	</ol>
</div>
<hr>

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
!pip install surprise
import pandas as pd
!pip install openpyxl
from surprise import Reader, SVD, Dataset, accuracy
from surprise.model_selection import GridSearchCV, train_test_split, cross_validate
pd.set_option('display.max_columns', None)

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 772.0/772.0 kB 13.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for scikit-surprise: filename=scikit_surprise-1.1.3-cp310-cp310-linux_x86_64.whl size=3095439 sha256=b77dd196c5ee0d9b7ba243bd2b59a8ec7f533aa45d56b3d1aeb2f30de28b3609
  Stored in directory: /root/.cache/pip/wheels/a5/ca/a8/4e28def53797fdc4363ca4af740db15a9c2f1595ebc51fb445
Successfully built scikit-surprise
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
ratings_file = '/content/drive/MyDrive/Dataframes/movielens_dataset/ratings.csv'
movies_file = '/content/drive/MyDrive/Dataframes/movielens_dataset/movies.csv'

In [ ]:
df_ratings = pd.read_csv(ratings_file)
df_ratings.head()

userId  movieId  rating   timestamp
0       1       16     4.0  1217897793
1       1       24     1.5  1217895807
2       1       32     4.0  1217896246
3       1       47     4.0  1217896556
4       1       50     4.0  1217896523

In [ ]:
df_movies = pd.read_csv(movies_file)

df_movies.head()

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy

In [ ]:
movie_data = pd.merge(df_ratings, df_movies, on='movieId')

movie_data.head()

userId  movieId  rating   timestamp          title       genres
0       1       16     4.0  1217897793  Casino (1995)  Crime|Drama
1       9       16     4.0   842686699  Casino (1995)  Crime|Drama
2      12       16     1.5  1144396284  Casino (1995)  Crime|Drama
3      24       16     4.0   963468757  Casino (1995)  Crime|Drama
4      29       16     3.0   836820223  Casino (1995)  Crime|Drama

<h2> II. Data Preprocessing</h2>

In [ ]:
user_movie_df = movie_data.pivot_table(index=["userId"], columns=["title"], values="rating")

In [ ]:
user_movie_df.head()

title   '71 (2014)  'Hellboy': The Seeds of Creation (2004)  \
userId                                                        
1              NaN                                      NaN   
2              NaN                                      NaN   
3              NaN                                      NaN   
4              NaN                                      NaN   
5              NaN                                      NaN   

title   'Round Midnight (1986)  'Til There Was You (1997)  'burbs, The (1989)  \
userId                                                                          
1                          NaN                        NaN                 NaN   
2                          NaN                        NaN                 NaN   
3                          NaN                        NaN                 NaN   
4                          NaN                        NaN                 NaN   
5                          NaN                        NaN                 NaN   

title   'night Mother (1986)  (500) Days of Summer (2009)  \
userId                                                      
1                        NaN                          NaN   
2                        NaN                          NaN   
3                        NaN                          NaN   
4                        NaN                          NaN   
5                        NaN                          NaN   

title   *batteries not included (1987)  ...And Justice for All (1979)  \
userId                                                                  
1                                  NaN                            NaN   
2                                  NaN                            NaN   
3                                  NaN                            NaN   
4                                  NaN                            NaN   
5                                  NaN                            NaN   

title   10 (1979)  10 Items or Less (2006)  10 Things I Hate About You (1999)  \
userId                                                                          
1             NaN                      NaN                                NaN   
2             NaN                      NaN                                NaN   
3             NaN                      NaN                                NaN   
4             NaN                      NaN                                NaN   
5             NaN                      NaN                                NaN   

title   10 to Midnight (1983)  10,000 BC (2008)  100 Girls (2000)  \
userId                                                              
1                         NaN               NaN               NaN   
2                         NaN               NaN               NaN   
3                         NaN               NaN               NaN   
4                         NaN               NaN               NaN   
5                         NaN               NaN               NaN   

title   101 Dalmatians (1996)  \
userId                          
1                         NaN   
2                         NaN   
3                         NaN   
4                         NaN   
5                         NaN   

title   101 Dalmatians (One Hundred and One Dalmatians) (1961)  \
userId                                                           
1                                                     NaN        
2                                                     NaN        
3                                                     NaN        
4                                                     NaN        
5                                                     NaN        

title   101 Reykjavik (101 Reykjavík) (2000)  102 Dalmatians (2000)  \
userId                                                                
1                                        NaN                    NaN   
2                                        NaN                    NaN   
3                  

In [ ]:
movie_user_df = movie_data.pivot_table(index=["title"], columns=["userId"], values="rating")
movie_user_df.head()

userId                                   1    2    3    4    5    6    7    \
title                                                                        
'71 (2014)                               NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Hellboy': The Seeds of Creation (2004)  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Round Midnight (1986)                   NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Til There Was You (1997)                NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'burbs, The (1989)                       NaN  NaN  NaN  NaN  NaN  NaN  NaN   

userId                                   8    9    10   11   12   13   14   \
title                                                                        
'71 (2014)                               NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Hellboy': The Seeds of Creation (2004)  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Round Midnight (1986)                   NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Til There Was You (1997)                NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'burbs, The (1989)                       NaN  NaN  NaN  NaN  NaN  NaN  NaN   

userId                                   15   16   17   18   19   20   21   \
title                                                                        
'71 (2014)                               NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Hellboy': The Seeds of Creation (2004)  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Round Midnight (1986)                   NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Til There Was You (1997)                NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'burbs, The (1989)                       NaN  NaN  NaN  NaN  NaN  NaN  NaN   

userId                                   22   23   24   25   26   27   28   \
title                                                                        
'71 (2014)                               NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Hellboy': The Seeds of Creation (2004)  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Round Midnight (1986)                   NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Til There Was You (1997)                NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'burbs, The (1989)                       NaN  NaN  NaN  3.0  NaN  NaN  NaN   

userId                                   29   30   31   32   33   34   35   \
title                                                                        
'71 (2014)                               NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Hellboy': The Seeds of Creation (2004)  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Round Midnight (1986)                   NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Til There Was You (1997)                NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'burbs, The (1989)                       NaN  NaN  NaN  2.0  NaN  NaN  NaN   

userId                                   36   37   38   39   40   41   42   \
title                                                                        
'71 (2014)                               NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Hellboy': The Seeds of Creation (2004)  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Round Midnight (1986)                   NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Til There Was You (1997)                NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'burbs, The (1989)                       NaN  NaN  NaN  NaN  NaN  NaN  NaN   

userId                                   43   44   45   46   47   48   49   \
title                                                                        
'71 (2014)                               NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Hellboy': The Seeds of Creation (2004)  NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Round Midnight (1986)                   NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'Til There Was You (1997)                NaN  NaN  NaN  NaN  NaN  NaN  NaN   
'burbs, The (1989)                       NaN  NaN  NaN  NaN  NaN  NaN  NaN   

userId                                   50   51   52   53   54   55   56   \
title                                                                        
'71 (2014)     

<h2>III. Collaborative Filtering</h2> 

<h3>A. Introduction to Collaborative Filtering</h3>

Collaborative Filtering (CF) is a popular technique in recommendation systems that makes personalized recommendations by identifying the similarities between users or items based on their past interactions. It is based on the assumption that if two users have similar preferences for some items, they are likely to have similar preferences for other items as well. Similarly, if two items are preferred by the same set of users, they are likely to be similar or related in some way.

There are two main types of Collaborative Filtering: Memory-Based Collaborative Filtering and Model-Based Collaborative Filtering.

Memory-Based Collaborative Filtering uses the entire user-item interaction matrix to compute the similarity between users or items. The similarity between users or items is used to make predictions about the ratings that a user would give to an item that they have not yet interacted with. This approach is simple and easy to implement but does not scale well with large datasets.

Model-Based Collaborative Filtering, on the other hand, uses machine learning algorithms to learn a model from the user-item interaction data. This approach involves decomposing the user-item interaction matrix into latent factors using techniques such as Singular Value Decomposition (SVD) or matrix factorization. The model is then used to make predictions about the ratings that a user would give to an item that they have not yet interacted with. This approach scales well with large datasets and can handle sparse data better than Memory-Based Collaborative Filtering.

<h3>«Item-Based Collaborative Filtering»</h3>

In [ ]:
import numpy as np

def dot_product(vector1,vector2):
    thedotproduct=np.sum([vector1[k]*vector2[k] for k in range(0,len(vector1))])
    return(thedotproduct)

In [ ]:
def vector_norm(vector):
    thenorm=np.sqrt(dot_product(vector,vector))
    return(thenorm)

In [ ]:
def cosine_similarity(vector1,vector2):
    thedotproduct=dot_product(vector1,vector2)
    thecosine=thedotproduct/(vector_norm(vector1)*vector_norm(vector2))
    thecosine=np.round(thecosine, 4)
    return(thecosine)

In [ ]:
def get_item_recommendations(interaction,itemname):
    otherrows=[rowname for rowname in interaction.index if rowname!=itemname]
    otheritems=interaction.loc[otherrows,:]
    theitem=list(interaction.loc[itemname,:])
    similarities=[]
    for items in otheritems.index:
        similarities.append(cosine_similarity(theitem,list(otheritems.loc[items,:])))
    otheritems['similarities']=similarities
    return list(otheritems.sort_values(by='similarities',ascending=False).index)

In [ ]:
titles = list(movie_user_df.index)
filtered_titles = [title for title in titles if '300' in title]

In [ ]:
filtered_titles

['300 (2007)',
 '3000 Miles to Graceland (2001)',
 '300: Rise of an Empire (2014)',
 'Mystery Science Theater 3000: The Movie (1996)']

In [ ]:
item1=movie_user_df.loc['300 (2007)',:]
item3=movie_user_df.loc['Mystery Science Theater 3000: The Movie (1996)',:]
print(dot_product(item1, item3))

NameError: ignored

In [ ]:
get_item_recommendations(movie_user_df, 'Mystery Science Theater 3000: The Movie (1996)')[0:10]

["'71 (2014)",
 "'Hellboy': The Seeds of Creation (2004)",
 "'Round Midnight (1986)",
 "'Til There Was You (1997)",
 "'burbs, The (1989)",
 "'night Mother (1986)",
 '(500) Days of Summer (2009)',
 '*batteries not included (1987)',
 '...And Justice for All (1979)',
 '10 (1979)']

<h3>Developing a recommendation system that gives estimated ratings for a given user and movie, based on on single value decomposition by using Surprise Library.</h3>

In [ ]:
reader = Reader(rating_scale=(1, 5))

In [ ]:
data = Dataset.load_from_df(movie_data[['userId', 'movieId', 'rating']], reader)

In [ ]:
trainset, testset = train_test_split(data, test_size=.25)
svd_model = SVD()
svd_model.fit(trainset)

In [ ]:
predictions = svd_model.test(testset)

accuracy.rmse(predictions)

RMSE: 0.8710


0.8710006559120251

In [ ]:
cross_validate(svd_model, data, measures=['RMSE', 'MAE'], cv=5, verbose=True)

Evaluating RMSE, MAE of algorithm SVD on 5 split(s).

                  Fold 1  Fold 2  Fold 3  Fold 4  Fold 5  Mean    Std     
RMSE (testset)    0.8754  0.8722  0.8736  0.8620  0.8666  0.8699  0.0050  
MAE (testset)     0.6726  0.6703  0.6737  0.6665  0.6687  0.6703  0.0026  
Fit time          3.65    2.18    1.59    1.74    1.76    2.19    0.76    
Test time         0.70    0.30    0.20    0.34    0.16    0.34    0.19    


{'test_rmse': array([0.87537385, 0.87216596, 0.8736078 , 0.86196494, 0.86661149]),
 'test_mae': array([0.67264498, 0.67025255, 0.673659  , 0.6664554 , 0.66866726]),
 'fit_time': (3.6521682739257812,
  2.181601047515869,
  1.5932197570800781,
  1.743455410003662,
  1.7591545581817627),
 'test_time': (0.6972658634185791,
  0.30457305908203125,
  0.20020747184753418,
  0.34304237365722656,
  0.1625056266784668)}

In [ ]:
svd_model.predict(uid=7.0, iid=541, verbose=True)

user: 7.0        item: 541        r_ui = None   est = 3.96   {'was_impossible': False}


Prediction(uid=7.0, iid=541, r_ui=None, est=3.961471029724566, details={'was_impossible': False})

In [ ]:
param_grid = {'n_epochs': [5, 10], 'lr_all': [0.002, 0.005]}

gs = GridSearchCV(SVD,
                  param_grid,
                  measures=['rmse', 'mae'],
                  cv=3,
                  n_jobs=-1,
                  joblib_verbose=True)

gs.fit(data)
gs.best_score['rmse']

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done  12 out of  12 | elapsed:   10.5s finished


0.8810359079379423

In [ ]:
gs.best_params['rmse']

{'n_epochs': 10, 'lr_all': 0.005}

In [ ]:
svd_model = SVD(**gs.best_params['rmse'])

data = data.build_full_trainset()
svd_model.fit(data)

svd_model.predict(uid=1.0, iid=541, verbose=True)

user: 1.0        item: 541        r_ui = None   est = 4.13   {'was_impossible': False}


Prediction(uid=1.0, iid=541, r_ui=None, est=4.13004221612804, details={'was_impossible': False})